In [1]:
import pandas as pd 
import numpy as np
from bertopic import BERTopic

#load data 
import pandas as pd 
 
df = pd.read_csv("./data_fixed.csv", engine='python',sep='^')
#df = df.astype(str)
docs= []
valueList = df.values.tolist()
for value in valueList:
    docs.append(value[0])

#print(df['texts'])
#df_updated = df.replace(to_replace ='<span\b[^>]*>(.*?)', value ='', regex=True)
#df_final = df_updated.replace(to_replace ='<\/span>',value='', regex=True)


#df_updated.to_csv('teste.csv', encoding='utf-8', index=False)
#df['nova_descricao'] = df['nova_descricao'].str.replace('[,.:;!?]+', ' ', regex=True).copy()
#df['nova_descricao'] = df['nova_descricao'].str.replace ('[/<>()|\+\-\$%&#@\'\"]+', ' ', regex=True).copy()
#df['nova_descricao'] = df['nova_descricao'].str.replace('[0-9]+', '', regex=True).copy()


In [2]:
# create model 
 
from sklearn.feature_extraction.text import CountVectorizer
from nltk.corpus import stopwords 
pt_stopwords = stopwords.words('portuguese')


# we add this to remove stopwords
vectorizer_model = CountVectorizer(strip_accents='ascii',ngram_range=(1, 2), stop_words=pt_stopwords)

model = BERTopic(
    vectorizer_model=vectorizer_model,
    language='portuguese', calculate_probabilities=True,
    verbose=True
)

#convert to list 
#docs = df.values.tolist()
 
topics, probabilities = model.fit_transform(docs)


Batches: 100%|██████████| 79/79 [00:54<00:00,  1.45it/s]
2023-02-13 12:25:38,076 - BERTopic - Transformed documents to Embeddings
2023-02-13 12:25:57,926 - BERTopic - Reduced dimensionality
2023-02-13 12:25:58,632 - BERTopic - Clustered reduced embeddings


In [3]:
model.get_topic_freq().head(11)

Topic  Count
0      -1    852
1       0     82
2       1     66
3       2     61
4       3     55
5       4     52
6       5     52
7       6     51
8       7     42
9       8     42
10      9     42

In [4]:
model.get_topic(0)

[('congresso nacional', 0.03915767659822488),
 ('congresso', 0.03900041298091825),
 ('dias', 0.033049613974111644),
 ('nacional', 0.02808549701394907),
 ('prazo', 0.0221607010406251),
 ('casa', 0.01814529425231586),
 ('sessao', 0.017907276653903927),
 ('votacao', 0.01710918720565445),
 ('comissao', 0.014385932956074538),
 ('projeto', 0.013919220167566804)]

In [5]:
model.get_topic_info()

Topic  Count                                               Name
0      -1    852                          -1_lei_federal_estado_art
1       0     82       0_congresso nacional_congresso_dias_nacional
2       1     66                 1_direito_direitos_politicos_dados
3       2     61  2_ministerio publico_ministerio_organizacao_pu...
4       3     55        3_tribunal_juizes_superior_tribunal justica
..    ...    ...                                                ...
60     59     11       59_militar_justica militar_militares_justica
61     60     11            60_radiodifusao_imagens_radio_televisao
62     61     11                 61_cargo_empregos_funcoes_afastado
63     62     11              62_petroleo_derivados_gas_gas natural
64     63     11   63_ingresso_profissionais_cursos_aperfeicoamento

[65 rows x 3 columns]

In [6]:
model.visualize_topics()


In [7]:
model.visualize_barchart()


In [8]:
model.visualize_heatmap()


In [9]:
from scipy.cluster import hierarchy as sch
# Hierarchical topics
linkage_function = lambda x: sch.linkage(x, 'single', optimal_ordering=True)
hierarchical_topics = model.hierarchical_topics(docs, linkage_function=linkage_function)
model.visualize_hierarchy(hierarchical_topics=hierarchical_topics)

100%|██████████| 63/63 [00:00<00:00, 120.79it/s]


In [10]:
tree = model.get_topic_tree(hierarchical_topics)
print(tree)

.
├─■──desde_sorteios propaganda_resolucoes disponham_perpetuo crueis_peculiaridades cargos ── Topic: 19
└─lei_federal_nao_nacional_uniao
     ├─lei_federal_nao_nacional_tribunal
     │    ├─■──petroleo_derivados_gas_gas natural_natural ── Topic: 62
     │    └─lei_federal_nao_nacional_tribunal
     │         ├─lei_federal_nao_nacional_tribunal
     │         │    ├─radio_televisao_radio televisao_partido_partidario
     │         │    │    ├─■──radiodifusao_imagens_radio_televisao_emissoras ── Topic: 60
     │         │    │    └─■──partido_partidario_partidos_fundo partidario_partidos politicos ── Topic: 43
     │         │    └─lei_federal_nao_nacional_tribunal
     │         │         ├─■──lei_sobre lei_capacidade_dispora sobre_dispora ── Topic: 51
     │         │         └─lei_federal_nao_nacional_tribunal
     │         │              ├─lei_federal_nao_nacional_tribunal
     │         │              │    ├─lei_federal_nao_tribunal_municipios
     │         │              │    │ 

In [11]:

from sentence_transformers import SentenceTransformer

sentence_model = SentenceTransformer("paraphrase-multilingual-MiniLM-L12-v2")
embeddings = sentence_model.encode(docs, show_progress_bar=False)


model.visualize_hierarchical_documents(docs, hierarchical_topics, embeddings=embeddings)



In [12]:
from umap import UMAP
reduced_embeddings = UMAP(n_neighbors=10, n_components=2, min_dist=0.0, metric='cosine').fit_transform(embeddings)
model.visualize_hierarchical_documents(docs, hierarchical_topics, reduced_embeddings=reduced_embeddings)